### Importing modules

In [1]:
"magic line  using inline or notebook"
%matplotlib inline
import matplotlib.pyplot as plt
import pandas as pd
import folium 
import json
import numpy as np

#for the lengende
from branca.element import Template, MacroElement

from folium import Choropleth, Circle, Marker


#imports for the lengende
from branca.element import Template, MacroElement
from folium.plugins import MarkerCluster
from folium import plugins

#imports for geojson
import geopandas as gpd
from folium.features import GeoJsonPopup

from pathlib import Path


### Read the Exel File

In [2]:
df1 =pd.read_excel('waterpoints.xlsx')

## The Map

In [3]:
#meakers color 
def status_color(color):
    if color=='operational'or color ==' ':
        return 'blue'
    elif color=='seasonal':
        return 'green'
    elif color=='needs repairs':
        return 'red'

In [5]:
# icon create funtion for the cluster 
icon_create_function = """
    function(cluster) {
    var childCount = cluster.getChildCount(); 
    var c = ' marker-cluster-';
    c += 'medium';

    return new L.DivIcon({ html: '<div><span>' + childCount + '</span></div>', className: 'marker-cluster' + c, iconSize: new L.Point(40, 40) });
    }
    """

# use to speedup  the rendering 
class MarkerClusterScript(MarkerCluster):
    def __init__(self, data, callback):
        from jinja2 import Template
        super(MarkerClusterScript, self).__init__([])
        self._name = 'Script'
        self._data = data
        if callable(callback):
            from flexx.pyscript import py2js
            self._callback =  py2js(callback, new_name="callback")
        else:
            self._callback = "var callback = {};".format(_callback)

        self._template = Template(u"""
{% macro script(this, kwargs) %}
(function(){
    var data = {{this._data}};
    var map = {{this._parent.get_name()}};
    var cluster = L.markerClusterGroup();
    {{this._callback}}

    for (var i = 0; i < data.length; i++) {
        var row = data[i];
        var marker = callback(row);
        marker.addTo(cluster);
    }

    cluster.addTo(map);
})();
{% endmacro %}
            """)

#creating the Map 

mymap = folium.Map(location=[7.5594, 30.5713], zoom_start= 6, tiles=None)

#map tilelayer
folium.raster_layers.TileLayer(tiles='openstreetmap', name='Select an Year', control=False, opacity=0.7).add_to(mymap)

#read the geofile for south-Sudan
with open('world-countries.json') as handle:
    country_geo = json.loads(handle.read())
for i in country_geo['features']:
    if i['properties']['name'] == 'South Sudan':
        country = i
        break

#adding the border
folium.GeoJson(country, name='Remove the Border').add_to(mymap)
folium.TileLayer('openstreetmap').add_to(mymap)


#clustering the markers 
mCluster = MarkerCluster(icon_create_function=icon_create_function, overlay=False,control=False).add_to(mymap)

############################################################

#marker in the Map
for _,city in df1.iterrows():
    #print(row)
    extand = "{border: 1px solid black;}"
    html =f"""<style>
table, th, td {extand}
</style>
<body>
<table>
     <caption style="margin-bottom:10px;">Waterpoints Information</caption>
    <tr>
        <th scope="row">Country</th>
        <td style="text-align: center">{city['County']}</td>
    </tr>
    <tr>
        <th scope="row">Coordinations</th>
        <td style="text-align: center">{city['dms']}</td>
    </tr>
    <tr>
        <th scope="row">Status</th>
        <td style="text-align: center">{city['Status']}</td>
    </tr>
    <tr>
        <th scope="row">Date of Installation</th>
        <td style="text-align: center">{city['year']}</td>
    </tr>

</table>
"""
    
    iframe = folium.IFrame(html, width=320, height=150)
    popup = folium.Popup(iframe, max_width=350, max_height=180)
    #logo_icon =folium.features.CustomIcon(image, icon_size=(18,30))
    marker = folium.Marker( location=[city['Latitude'], city['Longitude']], popup=popup, icon=folium.Icon(color=status_color(city['Status']), icon="tint",prefix='fa'))
    mCluster.add_child(marker)

    

############################################################

#html lengend
legend_template = """
{% macro html(this, kwargs) %}

<!doctype html>
<html lang="en">
<head>
  <meta charset="utf-8">
  <meta name="viewport" content="width=device-width, initial-scale=1">
  <title>jQuery UI Draggable - Default functionality</title>
  <link rel="stylesheet" href="//code.jquery.com/ui/1.12.1/themes/base/jquery-ui.css">

  <script src="https://code.jquery.com/jquery-1.12.4.js"></script>
  <script src="https://code.jquery.com/ui/1.12.1/jquery-ui.js"></script>
  
  <script>
  $( function() {
    $( "#maplegend" ).draggable({
                    start: function (event, ui) {
                        $(this).css({
                            right: "auto",
                            top: "auto",
                            bottom: "auto"
                        });
                    }
                });
});

  </script>
</head>
<body>

 
<div id='maplegend' class='maplegend' 
    style='position: absolute; z-index:9999; border:2px solid grey; background-color:rgba(255, 255, 255, 0.7);
     border-radius:6px; padding: 10px; font-size:14px; right: 20px; bottom: 20px;'>
     
<div class='legend-title'>State Population</div>
<div class='legend-scale'>
  <ul class='legend-labels'>
 <li><span style='background:blue;opacity:0.7;'></span>Operational</li>
    <li><span style='background:green;opacity:0.7;'></span>Seasonal</li>
    <li><span style='background:red;opacity:0.7;'></span>Need repairs</li>
  </ul>
</div>
</div>
 
</body>
</html>

<style type='text/css'>
  .maplegend .legend-title {
    text-align: left;
    margin-bottom: 5px;
    font-weight: bold;
    font-size: 90%;
    }
  .maplegend .legend-scale ul {
    margin: 0;
    margin-bottom: 5px;
    padding: 0;
    float: left;
    list-style: none;
    }
  .maplegend .legend-scale ul li {
    font-size: 80%;
    list-style: none;
    margin-left: 0;
    line-height: 18px;
    margin-bottom: 2px;
    }
  .maplegend ul.legend-labels li span {
    display: block;
    float: left;
    height: 16px;
    width: 30px;
    margin-right: 5px;
    margin-left: 0;
    border: 1px solid #999;
    }
  .maplegend .legend-source {
    font-size: 80%;
    color: #777;
    clear: both;
    }
  .maplegend a {
    color: #777;
    }
</style>
{% endmacro %}"""

macro = MacroElement()
macro._template = Template(legend_template)

mymap.get_root().add_child(macro)
mymap